# Send a UDF to a clean room from a stage

This notebook demonstrates how a provider can upload Python code to a stage, then upload the code from the stage to a clean room.
After you create your clean room, open this notebook in the provider account that created the clean room and follow the instructions below.

For more context, read [the Snowflake documentation](https://docs.snowflake.com/user-guide/cleanrooms/demo-flows/custom-code)

First, save your UDP to a "local" directory. Next, You'll upload it to a stage.

In [ ]:
with open('reverser.py','w') as f:
    f.write("""
import numpy as np
def main(some_string):
  '''Return the reverse of a string plus a random number 1-10'''
  return some_string[::-1] + str(np.random.randint(1,10))
"""
)
f.close()

try:
    print('Reading file content:')
    with open('reverser.py', 'r') as file:
        content = file.read()
        print(content)
except FileNotFoundError:
    print(f"Error: File not found at {file_path}")
except Exception as e:
    print(f"An error occurred: {e}")

Next, get the name of the stage for your clean room.

In [ ]:
USE WAREHOUSE app_wh;
USE ROLE samooha_app_role;

SET cleanroom_name = 'UDF example';
CALL samooha_by_snowflake_local_db.provider.get_stage_for_python_files($cleanroom_name);

To copy your file to the stage, copy the stage location above into the PUT command below.

In [ ]:
from snowflake.snowpark.context import get_active_session
session = get_active_session()

put_result = session.file.put('reverser.py','<STAGE_PATH>', auto_compress= False, overwrite=True)
put_result[0].status

Load the staged UDF file into the clean room.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.load_python_into_cleanroom(
    $cleanroom_name,
    'reverse', 
    ['some_string  STRING'],   
    ['numpy'],                 
    ['/reverser.py'],  
    'STRING',          
    'reverser.main'    
);

Uploading code causes the patch number to increase, so you'll need to update the default version.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive($cleanroom_name, 'V1_0', <NEW_PATCH_NUMBER>);

Now update the basic template in the clean room to add this new function.

In [ ]:
SET udf_template_name = 'basic_UDF_template';
CALL samooha_by_snowflake_local_db.provider.add_custom_sql_template(
    $cleanroom_name, 
    $udf_template_name,
    $$
    SELECT
      p.status,
      cleanroom.reverse(p.status),
      cleanroom.get_next_status(p.status) AS NEXT_STATUS,
    FROM SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS AS p
    LIMIT 100;
    $$
);

Finally, run `basic_UDF_template` from your consumer account to call your function.